In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_gross_profit_sii = generate_df_for_stocktype(107, 2, 3, 'sii', 'GrossProfitMargin', '毛利率(%)(營業毛利)/(營業收入)', '營益分析彙總表')

df_gross_profit_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



毛利率(%)(營業毛利)/(營業收入)
year: 107
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 2


公司代號     公司名稱 GrossProfitMargin(%)_107Q2 GrossProfitMargin(%)_107Q1  \
0    1101       台泥                      27.93                      23.95   
1    1102       亞泥                      23.92                      20.09   
2    1103       嘉泥                      14.47                      11.63   
3    1104     環球水泥                      11.46                      11.88   
4    1108     幸福水泥                       3.70                       2.47   
5    1109     信大水泥                      29.27                      22.71   
6    1110       東泥                       8.58                       8.35   
7    1201     味全公司                      30.19                      28.20   
8    1203     味王公司                      32.76                      33.75   
9    1210     大成長城                      14.25                      14.90   
10   1213       大飲                      10.39                      10.74   
11   1215     卜蜂企業                      13.20                      14.78   
12   1216       統一                      34.10                      33.97   
13   1217      愛之味                      33.01                      31.66   
14   1218     泰山企業                      17.79                      16.56   
15   1219     福壽實業                       8.66                       9.32   
16   1220       台榮                      13.74                      11.49   
17   1225      福懋油                       8.81                       8.99   
18   1227       佳格                      29.62                      30.87   
19   1229     聯華實業                      16.45                      16.62   
20   1231     聯華食品                      20.48                      22.76   
21   1232      大統益                      10.61                      10.43   
22   1233       天仁                      57.91                      58.11   
23   1234       黑松                      24.24                      20.48   
24   1235       興泰                      -0.55                     -10.29   
25   1236     宏亞食品                      24.40                      28.20   
26   1256  鮮活果汁-KY                      33.88                      31.63   
27   1262    綠悅-KY                       2.25                       7.73   
28   1301       台塑                      17.89                      17.26   
29   1303     南亞塑膠                      16.28                      16.75   
30   1304       台聚                      12.24                      12.58   
31   1305       華夏                      22.62                      23.41   
32   1307     三芳化工                      21.61                      23.21   
33   1308       亞聚                       4.78                       5.87   
34   1309     台達化工                       7.81                       7.75   
35   1310       台苯                      14.46                      13.64   
36   1312     國喬石化                      17.73                      17.61   
37   1313       聯成                       6.79                       7.51   
38   1314      中石化                      13.96                      13.25   
39   1315     達新工業                      13.97                      14.33   
40   1316       上曜                      33.54                      32.49   
41   1319       東陽                      22.58                      23.43   
42   1321       大洋                       3.76                       6.76   
43   1323       永裕                      24.16                      23.66   
44   1324     地球工業                      16.51                      14.99   
45   1325       恒大                      11.55                      11.55   
46   1326       台化                      15.07                      15.92   
47   1337    再生-KY                     -11.83                     -12.37   
48   1338    廣華-KY                      24.47                      25.25   
49   1339       昭輝                      27.16                      30.02   
50   1340    勝悅-KY                      22.85                      28.59   
51   1402      遠東新                      21.85        

In [5]:
df_gross_profit_otc = generate_df_for_stocktype(107, 2, 3, 'otc', 'GrossProfitMargin', '毛利率(%)(營業毛利)/(營業收入)', '營益分析彙總表')

df_gross_profit_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



毛利率(%)(營業毛利)/(營業收入)
year: 107
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 2


公司代號    公司名稱 GrossProfitMargin(%)_107Q2 GrossProfitMargin(%)_107Q1  \
0    1258   其祥-KY                      14.74                      16.52   
1    1259      安心                      24.89                      24.35   
2    1264      德麥                      37.17                      37.15   
3    1333     恩得利                      10.66                      10.33   
4    1336      台翰                      14.52                      14.99   
5    1565    精華光學                      36.73                      36.64   
6    1566      捷邦                      12.80                      12.30   
7    1569      濱川                      17.83                      18.04   
8    1570    力肯實業                      24.14                      22.84   
9    1580    新麥企業                      39.54                      40.45   
10   1584    精剛精密                      -0.83                       2.92   
11   1586    和勤精機                      17.65                      16.47   
12   1591   駿吉-KY                      12.58                       7.48   
13   1593      祺驊                      27.18                      26.17   
14   1595    川寶科技                      27.92                      27.75   
15   1597      直得                      48.33                      47.83   
16   1599     宏佳騰                      20.25                      17.56   
17   1742      台蠟                     -16.21                       4.86   
18   1752      南光                      35.51                      34.89   
19   1777      生泰                      32.34                      32.91   
20   1781    合世生醫                       6.90                       5.30   
21   1784    訊聯生技                      57.21                      58.62   
22   1785     光洋科                      10.30                       9.27   
23   1787     福盈科                      33.17                      33.22   
24   1788    杏昌生技                      22.75                      21.84   
25   1795    美時製藥                      46.92                      45.86   
26   1799      易威                       9.84                       9.87   
27   1813     寶利徠                      16.07                      14.00   
28   1815    富喬工業                      27.85                      27.82   
29   2035    唐榮公司                      -0.79                      -1.72   
30   2061      風青                       5.10                       4.36   
31   2063      世鎧                      31.04                      32.17   
32   2064      晉椿                       8.20                       9.43   
33   2066      世德                      24.96                      23.34   
34   2067      嘉鋼                      17.48                      15.84   
35   2221    大甲永和                      26.22                      24.84   
36   2230      泰茂                      14.93                      12.48   
37   2233      宇隆                      39.54                      39.73   
38   2235      謚源                      22.53                      24.40   
39   2596    綠意開發                      43.23                      47.14   
40   2640     大車隊                      44.97                      46.91   
41   2641    正德海運                      22.95                      23.91   
42   2643      捷迅                       9.65                       9.65   
43   2718      晶悅                       1.28                       8.57   
44   2719     燦星旅                      12.60                      11.94   
45   2724   富驛-KY                       0.47                      -7.62   
46   2726   雅茗-KY                      52.87                      52.92   
47   2729    瓦城泰統                      54.08                      53.73   
48   2732    六角國際                      48.16                      49.21   
49   2734     易飛網                      16.60                      17.62   
50   2736      高野                      49.46                      52.48   
51   2740      天蔥                      46.79                      46.84   
52   2916    滿心企業             

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_gross_profit = pd.concat([df_gross_profit_sii,df_gross_profit_otc],axis=0, ignore_index=True)

df_gross_profit

公司代號     公司名稱 GrossProfitMargin(%)_107Q2 GrossProfitMargin(%)_107Q1  \
0     1101       台泥                      27.93                      23.95   
1     1102       亞泥                      23.92                      20.09   
2     1103       嘉泥                      14.47                      11.63   
3     1104     環球水泥                      11.46                      11.88   
4     1108     幸福水泥                       3.70                       2.47   
5     1109     信大水泥                      29.27                      22.71   
6     1110       東泥                       8.58                       8.35   
7     1201     味全公司                      30.19                      28.20   
8     1203     味王公司                      32.76                      33.75   
9     1210     大成長城                      14.25                      14.90   
10    1213       大飲                      10.39                      10.74   
11    1215     卜蜂企業                      13.20                      14.78   
12    1216       統一                      34.10                      33.97   
13    1217      愛之味                      33.01                      31.66   
14    1218     泰山企業                      17.79                      16.56   
15    1219     福壽實業                       8.66                       9.32   
16    1220       台榮                      13.74                      11.49   
17    1225      福懋油                       8.81                       8.99   
18    1227       佳格                      29.62                      30.87   
19    1229     聯華實業                      16.45                      16.62   
20    1231     聯華食品                      20.48                      22.76   
21    1232      大統益                      10.61                      10.43   
22    1233       天仁                      57.91                      58.11   
23    1234       黑松                      24.24                      20.48   
24    1235       興泰                      -0.55                     -10.29   
25    1236     宏亞食品                      24.40                      28.20   
26    1256  鮮活果汁-KY                      33.88                      31.63   
27    1262    綠悅-KY                       2.25                       7.73   
28    1301       台塑                      17.89                      17.26   
29    1303     南亞塑膠                      16.28                      16.75   
30    1304       台聚                      12.24                      12.58   
31    1305       華夏                      22.62                      23.41   
32    1307     三芳化工                      21.61                      23.21   
33    1308       亞聚                       4.78                       5.87   
34    1309     台達化工                       7.81                       7.75   
35    1310       台苯                      14.46                      13.64   
36    1312     國喬石化                      17.73                      17.61   
37    1313       聯成                       6.79                       7.51   
38    1314      中石化                      13.96                      13.25   
39    1315     達新工業                      13.97                      14.33   
40    1316       上曜                      33.54                      32.49   
41    1319       東陽                      22.58                      23.43   
42    1321       大洋                       3.76                       6.76   
43    1323       永裕                      24.16                      23.66   
44    1324     地球工業                      16.51                      14.99   
45    1325       恒大                      11.55                      11.55   
46    1326       台化                      15.07                      15.92   
47    1337    再生-KY                     -11.83                     -12.37   
48    1338    廣華-KY                      24.47                      25.25   
49    1339       昭輝                      27.16                      30.02   
50    1340    勝悅-KY                      22.85                      28.59   
51

In [7]:
#檢查column資料型態

#df_gross_profit.info() #non-null object
#df_gross_profit.dtypes #object
#df_gross_profit.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
GrossProfit(%)_107Q1    float64
GrossProfit(%)_106Q4    float64
GrossProfit(%)_106Q3    float64
GrossProfit(%)_106Q2    float64
GrossProfit(%)_106Q1    float64
GrossProfit(%)_105Q4    float64
GrossProfit(%)_105Q3    float64
GrossProfit(%)_105Q2    float64
GrossProfit(%)_105Q1    float64
GrossProfit(%)_104Q4    float64
GrossProfit(%)_104Q3    float64
GrossProfit(%)_104Q2    float64
GrossProfit(%)_104Q1    float64
dtype: object
'''

df_gross_profit = df_gross_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_gross_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                            int64
公司名稱                           object
GrossProfitMargin(%)_107Q2    float64
GrossProfitMargin(%)_107Q1    float64
GrossProfitMargin(%)_106Q4    float64
GrossProfitMargin(%)_106Q3    float64
GrossProfitMargin(%)_106Q2    float64
GrossProfitMargin(%)_106Q1    float64
GrossProfitMargin(%)_105Q4    float64
GrossProfitMargin(%)_105Q3    float64
GrossProfitMargin(%)_105Q2    float64
GrossProfitMargin(%)_105Q1    float64
GrossProfitMargin(%)_104Q4    float64
GrossProfitMargin(%)_104Q3    float64
GrossProfitMargin(%)_104Q2    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['GrossProfitMargin(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_gross_profit['Growth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_gross_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_gross_profit = df_gross_profit.merge(df_basicinfo, on='公司代號', how='inner')

df_gross_profit

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  GrossProfitMargin(%)_107Q2  GrossProfitMargin(%)_107Q1  \
0     1101       台泥                       27.93                       23.95   
1     1102       亞泥                       23.92                       20.09   
2     1103       嘉泥                       14.47                       11.63   
3     1104     環球水泥                       11.46                       11.88   
4     1108     幸福水泥                        3.70                        2.47   
5     1109     信大水泥                       29.27                       22.71   
6     1110       東泥                        8.58                        8.35   
7     1201     味全公司                       30.19                       28.20   
8     1203     味王公司                       32.76                       33.75   
9     1210     大成長城                       14.25                       14.90   
10    1213       大飲                       10.39                       10.74   
11    1215     卜蜂企業                       13.20                       14.78   
12    1216       統一                       34.10                       33.97   
13    1217      愛之味                       33.01                       31.66   
14    1218     泰山企業                       17.79                       16.56   
15    1219     福壽實業                        8.66                        9.32   
16    1220       台榮                       13.74                       11.49   
17    1225      福懋油                        8.81                        8.99   
18    1227       佳格                       29.62                       30.87   
19    1229     聯華實業                       16.45                       16.62   
20    1231     聯華食品                       20.48                       22.76   
21    1232      大統益                       10.61                       10.43   
22    1233       天仁                       57.91                       58.11   
23    1234       黑松                       24.24                       20.48   
24    1235       興泰                       -0.55                      -10.29   
25    1236     宏亞食品                       24.40                       28.20   
26    1256  鮮活果汁-KY                       33.88                       31.63   
27    1262    綠悅-KY                        2.25                        7.73   
28    1301       台塑                       17.89                       17.26   
29    1303     南亞塑膠                       16.28                       16.75   
30    1304       台聚                       12.24                       12.58   
31    1305       華夏                       22.62                       23.41   
32    1307     三芳化工                       21.61                       23.21   
33    1308       亞聚                        4.78                        5.87   
34    1309     台達化工                        7.81                        7.75   
35    1310       台苯                       14.46                       13.64   
36    1312     國喬石化                       17.73                       17.61   
37    1313       聯成                        6.79                        7.51   
38    1314      中石化                       13.96                       13.25   
39    1315     達新工業                       13.97                       14.33   
40    1316       上曜                       33.54                       32.49   
41    1319       東陽                       22.58                       23.43   
42    1321       大洋                        3.76                        6.76   
43    1323       永裕                       24.16                       23.66   
44    1324     地球工業                       16.51                       14.99   
45    1325       恒大                       11.55                       11.55   
46    1326       台化                       15.07                       15.92   
47    1337    再生-KY                      -11.83                      -12.37   
48    1338    廣華-KY                       24.47                       25.25   
49    1339       昭輝                       27.16         

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_gross_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_GrossProfitMargin.xlsx', 'GrossProfitMargin_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
